In [1]:
function filename_splitter(filename)
    
    fn_splitted = split(filename, "_")

    nozzle_RR = parse(Float64, fn_splitted[5][1:end-2])

    return nozzle_RR
end

filename_splitter (generic function with 1 method)

In [8]:
# tpx3 file naming convention:
#[file number]_[metal]_[facet]_[beam species]_[beam RR]_[laser RR]_[laser position]_[temperature]_[comment]_xxxxxx.tpx3

using Parameters

include("function_convert_and_process.jl")
include("TPX3_analysis_structs.jl")
version = "0.1.12"

parameters = pars()

parameters.data_path      = "F://B3Data//25.03.2023"

filename                  = "001_Pt_upper_1p5prcNO_100Hz_lp0_280C_000000"
parameters.filename_stem  = parameters.data_path * "/" * filename

#-------------------------------------------------------------------#
#-----------------        PARAMETER SECTION        -----------------#

parameters.write_bin      = false
parameters.write_txt      = false

parameters.mode           = 3
parameters.first_seconds  = 3.0

parameters.mode3_t0       = 5.0
parameters.mode3_tmax     = 5000.0

# TOF Parameters
parameters.tof_max        = 8e-6
parameters.tof_bin        = 10e-9
parameters.tof_gates      = [5.24, 5.36] .* 1e-6 # must be sorted!

# Image Parameters 
parameters.create_image   = true
parameters.image_x_laser  = 138
parameters.image_y_laser  = 97
parameters.image_x_offset = 2
parameters.image_y_offset = 0
parameters.image_x_width  = 6
parameters.image_y_width  = 10

# Incident Beam Parameters
parameters.beam_x_min     = 99
parameters.beam_x_max     = 112
parameters.beam_y_min     = 96
parameters.beam_y_max     = 108
parameters.beam_zscale    = 100

# Kinetic Trace create parameters
parameters.kt_max         = 1/filename_splitter(filename)[1]
parameters.kt_bin         = 10e-6
parameters.kt_nbins       = Int(floor(parameters.kt_max/parameters.kt_bin))
parameters.kt_length      = 1000
parameters.t_noz_laser    = 200e-6
parameters.t_laser_surf   = 17e-6

# Detect Signal in Real Time, not correlated with beam shots
parameters.realtime       = false
parameters.realtime_t0    = 360
parameters.realtime_bin   = 1e-1
parameters.realtime_tmax  = 900


# Laser and nozzle frequencies (Hz)
parameters.freq_nozzle    = filename_splitter(filename)[1]
parameters.freq_laser     = 100000.

parameters.chunk_size     = (500*1024*1024)÷8


println("selected file\t: ", filename)
BGhists, x_tof, tof_spec, x_kt, kin_traces, kin_traces_bg, rt_sig, rt_bg = convert_and_process(parameters);

selected file	: 001_Pt_upper_1p5prcNO_100Hz_lp0_280C_000000
filesize	: 1.946 GB
------------------------------------------------------------------------------------------
Start processing file
------------------------------------------------------------------------------------------
getting initial chunk
	 beam times in this chunk: 0.010608852 - 126.58666 seconds
getting chunk number 2
	 beam times in this chunk: 126.58666 - 254.28366 seconds
getting chunk number 3
	 beam times in this chunk: 254.28366 - 380.42935 seconds
getting chunk number 4
	 beam times in this chunk: 380.42935 - 505.324 seconds

done converting data

------------------------------------------------------------------------------------------
Processing time
	Absolute: 56.5	seconds
	Relative: 0.48	min/GB
Total exp. time	: 505.3	seconds
------------------------------------------------------------------------------------------


In [ ]:
#-------------------------   SAVE KINETIC TRACES   ----------------------------
# 1. CREATE FOLDERS

# check if Results Folder exists, if not, generate it
if "Results" ∉ readdir(parameters.data_path) 
    mkdir(parameters.data_path * "//Results")
end

# check if a subfolder for this data exists, if not, generate it
if filename ∉ readdir(parameters.data_path * "//Results") 
    mkdir(parameters.data_path * "//Results//" * filename)
end

storage_path = parameters.data_path * "//Results//" * filename * "//"

#------------------------------------------------------------------------------
# 2. SAVE KINETIC TRACES FOR ALL TOF GATES

imagepar_string = "pars_"*string(parameters.image_x_laser)*"_"*string(parameters.image_y_laser)*"_"*string(parameters.image_x_offset)*"_"*string(parameters.image_y_offset)*"_"*string(parameters.image_x_width)*"_"*string(parameters.image_y_width)

tofcounter    = 1
for i in 1:Int(size(parameters.tof_gates)[1]/2)
    
    # generate the title of the file

    tofstring = string(round(parameters.tof_gates[tofcounter]*1e6,digits=2)) * "_" * string(round(parameters.tof_gates[tofcounter+1]*1e6,digits=2))*"us_"
    timing = string(parameters.mode3_t0)*"_"*string(parameters.mode3_tmax)*"_"*string(parameters.kt_length)*"s_chunks_"
    title = "Trace_" * timing * tofstring * imagepar_string * ".txt"
    tofcounter += 2
    
    # format the traces and print the file
    
    kt_final    = reduce(vcat, transpose.(kin_traces[i]))
    printout    = vcat(transpose(x_kt), kt_final)
    writedlm(storage_path * title, printout)
end

#------------------------------------------------------------------------------
# 3. SAVE TOF SPECTRUM

toftitle = storage_path * "TOFspectrum_" * imagepar_string * ".txt"

writedlm(toftitle, [x_tof tof_spec])

In [10]:
#-------------------------  PLOT THE REAL TIME SIGNAL   ----------------------------

x_realtime = range(parameters.realtime_t0 + parameters.realtime_bin, parameters.realtime_tmax, step=parameters.realtime_bin)
plot(x_realtime, (rt_sig[1] .- rt_bg[1]), labels=:none)#, yscale=:log, seriestype=:scatter)

In [8]:
#-------------------------   PLOT KINETIC TRACES FOR DIFFERENT REAL TIMES   ----------------------------
nr_massgate = 1

p = plot()

for i in 1:findmin([8, size(kin_traces[nr_massgate])[1]])[1]
    
    xval = x_kt .+ (i-1) * x_kt[end]
    yval = kin_traces[nr_massgate][i] .- sum(kin_traces[nr_massgate][i][end-10:end])/11
    
    p = plot!(xval, yval, labels=:none, color=:black)
end

display(p)